In [2]:
import json
from functools import reduce
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random
from sklearn import preprocessing
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import random
import numpy as np
from functools import reduce

In [3]:
with open('./clawer/team_2017.json') as f:
    dic = json.load(f)

In [4]:
dic

{'2225': {'team_id': '2225',
  'team_url': 'http://igem.org/Team.cgi?team_id=2225',
  'team_name': 'Aachen',
  'wiki': 'http://2017.igem.org/Team:Aachen',
  'region': 'Europe',
  'country': 'Germany',
  'track': 'Environment',
  'kind': 'Collegiate',
  'application': 'Accepted',
  'section': 'Overgraduate\n',
  'title': 'Salt Vault\n',
  'abstract': 'Decreasing fresh water availability is not only a problem for desert climate regions like North-Africa and the Middle East, but also for European countries like Germany or the Netherlands, where water pollution is mainly caused by industry.\r\nWe are modifying the genome of Saccharomyces cerevisiae to increase the uptake of various ions into the cell and store these inside its vacuole. This will be achieved by upregulation of native (vacuolar) ion importers and knock-out of ion exporters. Furthermore, we are expressing heterologous genes from the plant Arabidopsis thaliana in yeast to improve vacuolar ion accumulation, thus creating a micr

In [5]:
long_str = ''

In [6]:
dic_keys = dic.keys()

In [7]:
str_arr = [dic[key]['abstract'] for key in dic.keys()]

In [8]:
str_arr

['Decreasing fresh water availability is not only a problem for desert climate regions like North-Africa and the Middle East, but also for European countries like Germany or the Netherlands, where water pollution is mainly caused by industry.\r\nWe are modifying the genome of Saccharomyces cerevisiae to increase the uptake of various ions into the cell and store these inside its vacuole. This will be achieved by upregulation of native (vacuolar) ion importers and knock-out of ion exporters. Furthermore, we are expressing heterologous genes from the plant Arabidopsis thaliana in yeast to improve vacuolar ion accumulation, thus creating a microbial dustbin.\r\nWith this newly generated library of genetically engineered yeasts, we hope to offer a novel way of treating water contaminated by industrial processes and store pollutants in our intracellular reservoir, the Salt Vault. Then this concept can be employed by industries facing problems with high pollution in their process water.\n',


In [9]:
long_str = reduce(lambda a,b:a+' '+b,str_arr)

In [10]:
word_arr = long_str.strip(' ').strip('\n')

In [11]:
def filter_fuc(a):
    if(a is '\n' or a is ' '):
        return False
    else:
        return True
        
word_arr = list(filter(filter_fuc,word_arr.split(' ')))

In [12]:
test_sentence = word_arr
CONTEXT_SIZE = 2
EMBEDDING_DIM = 10
# We will use Shakespeare Sonnet 2
# we should tokenize the input, but we will ignore that for now
# build a list of tuples.  Each tuple is ([ word_i-2, word_i-1 ], target word)
trigrams = [([test_sentence[i], test_sentence[i + 1]], test_sentence[i + 2])
            for i in range(len(test_sentence) - 2)]
# print the first 3, just so you can see what they look like
print(trigrams[:3])

vocab = set(test_sentence)
word_to_ix = {word: i for i, word in enumerate(vocab)}
word_to_ix['<unk>'] = len(word_to_ix)

class NGramLanguageModeler(nn.Module):

    def __init__(self, vocab_size, embedding_dim, context_size):
        super(NGramLanguageModeler, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.linear1 = nn.Linear(context_size * embedding_dim, 128)
        self.linear2 = nn.Linear(128, vocab_size)

    def forward(self, inputs):
        inputs__ = [x for x in inputs]
        inputs_ = torch.Tensor(inputs__)
        inputs_ = inputs_.long()
        embeds = self.embeddings(inputs_).view((1, -1))
        out = F.relu(self.linear1(embeds))
        out = self.linear2(out)
        log_probs = F.log_softmax(out, dim=1)
        return log_probs
trigrams = [([test_sentence[i], test_sentence[i + 1]], test_sentence[i + 2])
            for i in range(len(test_sentence) - 2)]

model = NGramLanguageModeler(len(word_to_ix), EMBEDDING_DIM,CONTEXT_SIZE)
'''
losses = []
loss_function = nn.NLLLoss()

optimizer = optim.SGD(model.parameters(), lr=0.001)
def filter_f(a):
    if(a is not 0):
        return True
    else:
        return False
for epoch in range(50):
    total_loss = torch.Tensor([0])
    for context, target in trigrams:

        # Step 1. Prepare the inputs to be passed to the model (i.e, turn the words
        # into integer indices and wrap them in variables)
        context_idxs = torch.Tensor(list(filter(filter_f,[word_to_ix[w] for w in context])))
        #context_idxs = torch.tensor([word_to_ix[w] for w in context])
        context_idx = context_idxs.long()
        # Step 2. Recall that torch *accumulates* gradients. Before passing in a
        # new instance, you need to zero out the gradients from the old
        # instance
        model.zero_grad()

        # Step 3. Run the forward pass, getting log probabilities over next
        # words
        log_probs = model.forward(context_idx)

        # Step 4. Compute your loss function. (Again, Torch wants the target
        # word wrapped in a variable)
        loss = loss_function(log_probs, torch.tensor([word_to_ix[target]], dtype=torch.long))

        # Step 5. Do the backward pass and update the gradient
        loss.backward()
        optimizer.step()
        #print(1)
        # Get the Python number from a 1-element Tensor by calling tensor.item()
        total_loss += loss.item()
    losses.append(total_loss)
    print(total_loss)
print(losses)  # The loss decreased every iteration over the training data!
'''

[(['Decreasing', 'fresh'], 'water'), (['fresh', 'water'], 'availability'), (['water', 'availability'], 'is')]


'\nlosses = []\nloss_function = nn.NLLLoss()\n\noptimizer = optim.SGD(model.parameters(), lr=0.001)\ndef filter_f(a):\n    if(a is not 0):\n        return True\n    else:\n        return False\nfor epoch in range(50):\n    total_loss = torch.Tensor([0])\n    for context, target in trigrams:\n\n        # Step 1. Prepare the inputs to be passed to the model (i.e, turn the words\n        # into integer indices and wrap them in variables)\n        context_idxs = torch.Tensor(list(filter(filter_f,[word_to_ix[w] for w in context])))\n        #context_idxs = torch.tensor([word_to_ix[w] for w in context])\n        context_idx = context_idxs.long()\n        # Step 2. Recall that torch *accumulates* gradients. Before passing in a\n        # new instance, you need to zero out the gradients from the old\n        # instance\n        model.zero_grad()\n\n        # Step 3. Run the forward pass, getting log probabilities over next\n        # words\n        log_probs = model.forward(context_idx)\n\n   

In [13]:
random.shuffle(word_arr)

In [14]:
word_dic = dict()
for index in range(len(word_arr)):
    word_dic[word_arr[index]] = index

In [15]:
def word2vec(word):
    vec = []
    for index in range(10):
       vec.append(ord(word[index%len(word)])) 
    return preprocessing.normalize(np.asarray(vec).reshape(1,-1))

In [16]:
word2vec('hello')

array([[0.30892785, 0.30001647, 0.32080969, 0.32080969, 0.32972107,
        0.30892785, 0.30001647, 0.32080969, 0.32080969, 0.32972107]])

In [17]:
word_arr = [w.strip(' ').strip(',').strip('\n') for w in word_arr]
def filter_no_zero(a):
    if(len(a) is 0):
        return False
    else:
        return True
word_arr = list(filter(filter_no_zero,word_arr))
word_set = set(word_arr)

In [18]:
vec_dic = dict()
for index in range(len(list(word_set))):
    vec_dic[list(word_set)[index]] = word2vec(list(word_set)[index])

In [19]:
def cal_sin_distance(a,b):
    return a.dot(b.reshape(-1,1))[0][0]

In [20]:
cal_sin_distance(vec_dic[list(vec_dic.keys())[0]],vec_dic[list(vec_dic.keys())[1]])

0.8875796277754773

In [29]:
dic_keys_arr = list(dic.keys())
team_arr_arr = []
def filter_no_zero(a):
    if(len(a) is 0):
        return False
    else:
        return True
for index in range(len(list(dic_keys_arr))):
    team_des_arr = dic[dic_keys_arr[index]]['abstract'].split(' ')
    team_des_arr = [w.strip(' ').strip('(').strip(')').strip(r'\W').strip(r'\s') for w in team_des_arr]
    team_des_arr = filter(filter_no_zero,team_des_arr)
    team_des_arr = list(map(lambda a:word2vec(a),team_des_arr))
    team_arr_arr.append(team_des_arr)

In [30]:
team_arr_arr

[[array([[0.21066569, 0.31290051, 0.30670446, 0.35317483, 0.31290051,
          0.30050841, 0.35627286, 0.32529261, 0.34078273, 0.31909656]]),
  array([[0.30041088, 0.33575333, 0.29746567, 0.33869854, 0.30630129,
          0.30041088, 0.33575333, 0.29746567, 0.33869854, 0.30630129]]),
  array([[0.3428868 , 0.27949597, 0.3342426 , 0.29102157, 0.32847979,
          0.3428868 , 0.27949597, 0.3342426 , 0.29102157, 0.32847979]]),
  array([[0.29494593, 0.35880021, 0.29494593, 0.31927137, 0.32839341,
          0.29494593, 0.29798661, 0.31927137, 0.32839341, 0.31927137]]),
  array([[0.31622777, 0.31622777, 0.31622777, 0.31622777, 0.31622777,
          0.31622777, 0.31622777, 0.31622777, 0.31622777, 0.31622777]]),
  array([[0.31022122, 0.31304141, 0.32714238, 0.31022122, 0.31304141,
          0.32714238, 0.31022122, 0.31304141, 0.32714238, 0.31022122]]),
  array([[0.31286479, 0.31004619, 0.30440898, 0.3410508 , 0.31286479,
          0.31004619, 0.30440898, 0.3410508 , 0.31286479, 0.31004619]]),